In [48]:
using JuMP
try import Mosek; using MosekTools; catch err; println("MOSEK not installed"); end
try import SCS;   catch err; println("SCS not installed"); end
try import SDPA;  catch err; println("SDPA not installed"); end
try import Clarabel; catch err; println("Clarabel not installed"); end

# Tasks:
# Write LP. Write in vectorized notation.
#Extract feasible point, optimal value, solver status, duality gap.
# Formulate dual (by hand). Solve.

# Next week:
# Formulate LP with *no* solution
# Extract infeasibility certificate.
# LP's for weighted matching, stable set,.. problems

SDPA not installed
Clarabel not installed


### PRIMAL

In [49]:
model = Model(Mosek.Optimizer)

A JuMP Model
├ solver: Mosek
├ objective_sense: FEASIBILITY_SENSE
├ num_variables: 0
├ num_constraints: 0
└ Names registered in the model: none

In [50]:
@variable(model, x[1:4])  # Note: you can directly add some constraints in the variable declaration, e.g. @variable(model, x[1:4] ≥ 0) 

4-element Vector{VariableRef}:
 x[1]
 x[2]
 x[3]
 x[4]

In [51]:
#@constraint(model,  [i=1:4], x[i] ≤ 1)
A = [1 2 3 4; 5 6 7 8]
b = [1; 2]
@constraint(model, A*x ≤ b)
c = [1; 2; 3; 4]
@objective(model, Max, c'*x);
print(model)

In [52]:
optimize!(model)

Problem
  Name                   :                 
  Objective sense        : maximize        
  Type                   : LO (linear optimization problem)
  Constraints            : 2               
  Affine conic cons.     : 0               
  Disjunctive cons.      : 0               
  Cones                  : 0               
  Scalar variables       : 4               
  Matrix variables       : 0               
  Integer variables      : 0               

Optimizer started.
Presolve started.
Linear dependency checker started.
Linear dependency checker terminated.
Eliminator started.
Freed constraints in eliminator : 1
Eliminator terminated.
Eliminator - tries                  : 1                 time                   : 0.00            
Lin. dep.  - tries                  : 1                 time                   : 0.00            
Lin. dep.  - primal attempts        : 1                 successes              : 1               
Lin. dep.  - dual attempts          : 0             

In [53]:
x_o = value.(x)

4-element Vector{Float64}:
 0.0
 0.0
 0.0
 0.25

In [54]:
α = objective_value(model)

1.0

In [55]:
solution_summary(model)

solution_summary(; result = 1, verbose = false)
├ solver_name          : Mosek
├ Termination
│ ├ termination_status : OPTIMAL
│ ├ result_count       : 2
│ ├ raw_status         : Mosek.MSK_SOL_STA_OPTIMAL, Mosek.MSK_SOL_STA_OPTIMAL
│ └ objective_bound    : 1.00000e+00
├ Solution (result = 1)
│ ├ primal_status        : FEASIBLE_POINT
│ ├ dual_status          : FEASIBLE_POINT
│ ├ objective_value      : 1.00000e+00
│ ├ dual_objective_value : 1.00000e+00
│ └ relative_gap         : 0.00000e+00
└ Work counters
  ├ solve_time (sec)   : 1.97440e-04
  ├ simplex_iterations : 0
  ├ barrier_iterations : 0
  └ node_count         : 0

#### Note: solution summary gave _minus_ the objective value, at least for SCS solver. Seems to be an SCS internal convention.

### DUAL - by hand

In [56]:
dual_model = Model(SCS.Optimizer)
@variable(dual_model, y[1:2])
@objective(dual_model, Min, b'y)
@constraint(dual_model, A'*y == c)
@constraint(dual_model, y .≥ 0)
print(dual_model)
optimize!(dual_model)

------------------------------------------------------------------
	       SCS v3.2.8 - Splitting Conic Solver
	(c) Brendan O'Donoghue, Stanford University, 2012
------------------------------------------------------------------
problem:  variables n: 2, constraints m: 6
cones: 	  z: primal zero / dual free vars: 4
	  l: linear vars: 2
settings: eps_abs: 1.0e-04, eps_rel: 1.0e-04, eps_infeas: 1.0e-07
	  alpha: 1.50, scale: 1.00e-01, adaptive_scale: 1
	  max_iters: 100000, normalize: 1, rho_x: 1.00e-06
	  acceleration_lookback: 10, acceleration_interval: 10
	  compiled with openmp parallelization enabled
lin-sys:  sparse-direct-amd-qdldl
	  nnz(A): 10, nnz(P): 0
------------------------------------------------------------------
 iter | pri res | dua res |   gap   |   obj   |  scale  | time (s)
------------------------------------------------------------------
     0| 3.95e+00  2.01e+00  4.80e-01  2.23e+00  1.00e-01  1.75e-03 
    25| 1.14e-07  5.98e-08  8.01e-09  1.00e+00  1.00e-01  1.8

In [57]:
y_o = value.(y)

2-element Vector{Float64}:
 0.9999999621566827
 4.674152138585949e-9

In [58]:
β = objective_value(dual_model)

0.9999999715049873

In [59]:
solution_summary(dual_model)

solution_summary(; result = 1, verbose = false)
├ solver_name          : SCS
├ Termination
│ ├ termination_status : OPTIMAL
│ ├ result_count       : 1
│ └ raw_status         : solved
├ Solution (result = 1)
│ ├ primal_status        : FEASIBLE_POINT
│ ├ dual_status          : FEASIBLE_POINT
│ ├ objective_value      : 1.00000e+00
│ └ dual_objective_value : 1.00000e+00
└ Work counters
  └ solve_time (sec)   : 1.79942e-03

In [60]:
# duality gap
β - α

-2.8495012682761e-8

### DUAL - with package

In [61]:
using Dualization
model2 = Model(Mosek.Optimizer)
@variable(model2, x[1:2] ≤ 1)
dual_model = dualize(model)
print(dual_model)